In [1]:
from IPython.display import display, SVG
from typing import Optional, Sequence
import dataclasses
import math
import enum

from typesetting import ParagraphItem, ParagraphItemType, Font, Glyph, hyphenate, text_to_paragraph_items, MAX_PENALTY, greedy_line_breaks
from typesetting.cairo import fill_glyphs_at

Source:

http://www.eprg.org/G53DOC/pdfs/knuth-plass-breaking.pdf

In [2]:
from faker import Faker
import textwrap

Faker.seed(0x01234567)
lorem = hyphenate("".join([
    "Difficult Quick Foxes with 1034 boxes. ",
    Faker(["en"]).paragraph(50)
]))
print(f"Generated lorem ipsum:\n\n{textwrap.fill(textwrap.shorten(lorem, 200), 72)}")
print(f"\nRepr of first part:\n{textwrap.shorten(lorem, 72)!r}")

Generated lorem ipsum:

Dif­fi­cult Quick Foxes with 1034 boxes. Ques­tion drug can­di­date.
Edge I mes­sage here. Ex­pert cold sci­en­tist can­di­date black brother
him. Worry per­haps talk pull blue let­ter. Gun [...]

Repr of first part:
'Dif\xadfi\xadcult Quick Foxes with 1034 boxes. Ques\xadtion drug [...]'


In [3]:
rm_face_path = "EBGaramond-VariableFont_wght.ttf"
#rm_face_path = "Raleway-VariableFont_wght.ttf"
#rm_face_path = "LibreBaskerville-Regular.ttf"
rm_size = 12
rm_font = Font(path=rm_face_path, em_size=[rm_size, rm_size], features=["onum"])

sm_rm_size = rm_size * 0.8
sm_rm_font = Font(path=rm_face_path, em_size=[sm_rm_size, sm_rm_size], features=["onum"])

In [4]:
import uniseg.linebreak
print(textwrap.fill("|".join(uniseg.linebreak.line_break_units(lorem)), 80))

Dif­|fi­|cult |Quick |Foxes |with |1034 |boxes. |Ques­|tion |drug
|can­|di­|date. |Edge |I |mes­|sage |here. |Ex­|pert |cold |sci­|en­|tist
|can­|di­|date |black |brother |him. |Worry |per­|haps |talk |pull |blue
|let­|ter. |Gun |choose |abil­|ity |fin­|ish. |Cut |decade |hun­|dred |whom
|short |past. |I |win |num­|ber |ta­|ble |party. |In­|di­|vid­|ual |laugh |end
|af­|fect |present |imag­|ine |body. |Hear |es­|tab­|lish |pay |go
|pol­|i­|tics. |Cell |re­|veal |sit |try |mem­|ory |own |op­|er­|a­|tion
|ma­|jor­|ity. |Player |old |ap­|ply |lan­|guage |hus­|band |ei­|ther. |Lawyer
|com­|mon |artist |space. |Through |tax |ac­|tion |ben­|e­|fit |pur­|pose |our
|you. |Change |they |trip |it­|self |grow |pol­|i­|tics |end |ar­|ti­|cle. |No
|an­|swer |in­|ter­|view |mil­|lion |oc­|cur. |Laugh |trade |your­|self |child
|reach |last. |Pic­|ture |push |owner |open |com­|mer­|cial |woman |space.
|Agree­|ment |re­|port |wrong |im­|por­|tant |source |tonight. |War
|op­|por­|tu­|nity |film |course 

In [5]:
para_items = list(text_to_paragraph_items(lorem, rm_font))

if False:
    print("First few items:")
    print("\n".join(textwrap.indent(f"{item!r}", "  ") for item in para_items[:10]))
    print("Final few items:")
    print("\n".join(textwrap.indent(f"{item!r}", "  ") for item in para_items[-10:]))

In [6]:
import io
from IPython.display import display, SVG
import cairo
from typing import Iterable

def render_lines(ctx: cairo.Context, line_break_idxs: Iterable[int], x0: float, y0: float, line_width: float):
    line_start_idx = 0
    for line_idx, line_end_idx in enumerate(line_break_idxs):
        x = x0
        y = line_height*line_idx + y0
        running_text, running_width = [], 0.0
    
        # What delta needs to be taken up by glue
        natural_width, total_stretch, total_shrink = 0.0, 0.0, 0.0
        for item in para_items[line_start_idx:line_end_idx]:
            if item.item_type == ParagraphItemType.PENALTY:
                continue
            natural_width += item.width
            if item.item_type == ParagraphItemType.GLUE:
                total_stretch += item.stretchability
                total_shrink += item.shrinkability
        if para_items[line_end_idx].item_type == ParagraphItemType.PENALTY:
            natural_width += para_items[line_end_idx].width
        delta = line_width - natural_width
    
        # Total slack for delta
        if delta > 0.0:
            adjustment_ratio = delta / total_stretch if total_stretch > 0 else math.inf
        elif delta < 0.0:
            adjustment_ratio = delta / total_shrink if total_shrink > 0 else math.inf
        else:
            adjustment_ratio = 0.0

        fill_glyphs_at(ctx, x + line_width + rm_font.em_size[0], y, sm_rm_font.shape(f"{adjustment_ratio:.2f}"), sm_rm_font)

        adjustment_ratio = max(-1.0, adjustment_ratio)
        for item_idx in range(line_start_idx, line_end_idx+1):
            item = para_items[item_idx]
            if item_idx != line_end_idx and item.item_type == ParagraphItemType.PENALTY:
                continue
            if item_idx == line_end_idx and item.item_type == ParagraphItemType.GLUE:
                continue
            running_width += item.width
            if item.item_type == ParagraphItemType.GLUE:
                text = "".join(running_text)
                fill_glyphs_at(ctx, x, y, rm_font.shape(text), rm_font)
                x += running_width
                if adjustment_ratio > 0:
                    x += item.stretchability * adjustment_ratio
                else:
                    x += item.shrinkability * adjustment_ratio
    
                running_text, running_width = [], 0.0
            else:
                running_text.append(item.text)
        text = "".join(running_text)
        if text != "":
            fill_glyphs_at(ctx, x, y, rm_font.shape(text), rm_font)
        line_start_idx = line_end_idx+1

In [7]:
from typing import Optional
from collections import namedtuple

class FitnessClass(enum.IntEnum):
    TIGHT = 0
    NORMAL = 1
    LOOSE = 2
    VERY_LOOSE = 3

@dataclasses.dataclass(frozen=True, eq=True, order=True)
class NodeKey:
    # Index of line this break appears on. -1 == start of para
    line_idx: int = -1

    # Index of para item corresponding to this line break. None == start of para
    item_idx: Optional[int] = None

    # Fitness class of this line.
    fitness_class: FitnessClass = FitnessClass.NORMAL

@dataclasses.dataclass(frozen=True, eq=True)
class NodeData:
    total_width: float = 0.0
    total_stretch: float = 0.0
    total_shrink: float = 0.0
    total_demerits: float = 0.0

    previous: Optional[tuple[NodeKey, "NodeData"]] = None

In [8]:
line_width = 5 * 72

In [9]:
import math
from collections import defaultdict
from sortedcontainers import SortedSet, SortedDict

# Mapping of active node keys to their data.
active_nodes: SortedDict[NodeKey, NodeData] = SortedDict()

# All nodes which were ever activated.
all_nodes: dict[NodeKey, set[NodeData]] = defaultdict(set)

def activate_node_if_better(key: NodeKey, data: NodeData):
    """
    Add or replace a node in the active nodes list if there is no existing
    active node for the key or if the fitness of the node is better than
    the existing active node for the key.
    """
    all_nodes[key].add(data)
    existing_active = active_nodes.get(key)
    if existing_active is None or existing_active.total_demerits > data.total_demerits:
        active_nodes[key] = data

def deactivate_node(key: NodeKey):
    """
    Deactivate a previously active node.
    """
    del active_nodes[key]

# Create active node representing beginning of paragraph
activate_node_if_better(NodeKey(), NodeData())

# Parameters for optimisation algorithm
upper_adjustment_ratio = 4.0
extra_flag_penalty = 50
line_penalty = 10
mismatched_fitness_penalty = 10
optimise_fitness_classes = True

# State of optimisation algorithm.
sum_width, sum_stretch, sum_shrink = 0.0, 0.0, 0.0
prev_was_box = False

for end_idx, item in enumerate(para_items):
    is_feasible_breakpoint = False
    
    if item.item_type == ParagraphItemType.GLUE:
        is_feasible_breakpoint = prev_was_box
    elif item.item_type == ParagraphItemType.PENALTY:
        is_feasible_breakpoint = item.penalty < MAX_PENALTY

    if is_feasible_breakpoint:
        feasible_breaks: set[tuple[NodeKey, NodeData]] = set()
        nodes_to_deactivate: set[NodeKey] = set()
        for node_key, node_data in active_nodes.items():
            # Compute natural width of line from node to current brrakpoint.
            natural_width = sum_width - node_data.total_width
            if item.item_type == ParagraphItemType.PENALTY:
                natural_width += item.width

            # Compute adjustment ratio implied by line.
            if natural_width < line_width:
                line_stretch = sum_stretch - node_data.total_stretch
                adjustment_ratio = (line_width - natural_width)/line_stretch if line_stretch > 0 else math.inf
            elif natural_width > line_width:
                line_shrink = sum_shrink - node_data.total_shrink
                adjustment_ratio = (line_width - natural_width)/line_shrink if line_shrink > 0 else math.inf
            else:
                adjustment_ratio = 0.0

            # Compute total penalty for breaking line at this point.
            penalty = item.penalty

            # If the previous line break was flagged and this line break
            # was flagged, add an additional penalty.
            if node_key.item_idx is not None:
                prev_item = para_items[node_key.item_idx]
                if item.flagged and prev_item.flagged:
                    penalty += extra_flag_penalty

            # Compute fitness class of this line.
            if optimise_fitness_classes:
                if adjustment_ratio < -0.5:
                    fitness_class = FitnessClass.TIGHT
                elif adjustment_ratio < 0.5:
                    fitness_class = FitnessClass.NORMAL
                elif adjustment_ratio < 1.0:
                    fitness_class = FitnessClass.LOOSE
                else:
                    fitness_class = FitnessClass.VERY_LOOSE
            else:
                fitness_class = FitnessClass.NORMAL
            
            # If we move more than 1 step of fitness class, add penalty.
            #if abs(node_key.fitness_class - fitness_class) > 1:
            penalty += mismatched_fitness_penalty * abs(node_key.fitness_class - fitness_class)

            # Add a fixed penalty for breaking lines.
            penalty += line_penalty
            
            # Deactivate nodes where we're considering endpoints so far
            # away that glue would have to be shrunken too far or if this breakpoint
            # is a forced breakpoint and so later lines could never start at the node.
            did_deactivate_node = False
            if adjustment_ratio < -1.0 or item.penalty <= -MAX_PENALTY:
                nodes_to_deactivate.add(node_key)

                # If this would remove all active nodes, make sure we record the
                # next break as feasible. This is a "break of last resort" to make
                # sure we find _some_ solution.
                if len(nodes_to_deactivate) == len(active_nodes):
                    adjustment_ratio = -1.0
            
            # Compute demerit for this line.
            if penalty >= 0.0:
                demerit = (1.0 + 100.0 * (abs(adjustment_ratio) ** 3.0) + penalty) ** 2.0
            elif min(penalty, item.penalty) > -MAX_PENALTY:
                demerit = (1.0 + 100.0 * (abs(adjustment_ratio) ** 3.0)) ** 2.0 - (penalty ** 2.0)
            else:
                demerit = (1.0 + 100.0 * (abs(adjustment_ratio) ** 3.0)) ** 2.0

            # Compute total demerits and store running sums for this break.
            total_demerits = demerit + node_data.total_demerits
                
            total_width = sum_width
            total_stretch, total_shrink = sum_stretch, sum_shrink
            if item.item_type == ParagraphItemType.GLUE:
                total_stretch += item.stretchability
                total_shrink += item.shrinkability
            if item.item_type != ParagraphItemType.PENALTY:
                total_width += item.width

            break_node_key = NodeKey(
                line_idx=node_key.line_idx + 1,
                item_idx=end_idx,
                fitness_class=fitness_class,
            )
            break_node_data = NodeData(
                total_width=total_width,
                total_stretch=total_stretch,
                total_shrink=total_shrink,
                total_demerits=total_demerits,
                previous=(node_key, node_data),
            )

            # If this line is not stretched or shrunk too much, record it as a feasible breakpoint.
            if adjustment_ratio >= -1.0 and adjustment_ratio < upper_adjustment_ratio:
                feasible_breaks.add((break_node_key, break_node_data))

        # Deactivate nodes we no-longer need.
        for nk in nodes_to_deactivate:
            deactivate_node(nk)

        # Activate best feasible breaks.
        for nk, nd in feasible_breaks:
            activate_node_if_better(nk, nd)

    # Update running sums
    if item.item_type != ParagraphItemType.PENALTY:
        sum_width += item.width
    if item.item_type == ParagraphItemType.GLUE:
        sum_stretch += item.stretchability
        sum_shrink += item.shrinkability

    # Update flag indicating if the previous item was a box.
    prev_was_box = item.item_type == ParagraphItemType.BOX

# Show stats.
print(f"Remaining active node count: {len(active_nodes)}")
optimal_node: Optional[tuple[NodeKey, NodeData]] = None
for nk, nd in active_nodes.items():
    # We only care about end nodes.
    assert nk.item_idx == len(para_items) - 1
    if optimal_node is None or nd.total_demerits < optimal_node[1].total_demerits:
        optimal_node = (nk, nd)
assert optimal_node is not None

print(f"Optimal demerit {optimal_node[1].total_demerits:,.0f}")
optimal_line_break_idxs = []

node_keys_on_best_path: set[NodeKey] = set()
node = optimal_node
while node is not None:
    nk, nd = node
    node_keys_on_best_path.add(nk)
    if nk.item_idx is not None:
        optimal_line_break_idxs.append(nk.item_idx)
    node = nd.previous
optimal_line_break_idxs = list(reversed(optimal_line_break_idxs))

Remaining active node count: 4
Optimal demerit 114,999


In [10]:
from graphviz import Digraph
dot = Digraph()
dot.graph_attr["rankdir"] = "LR"

all_node_items = list(all_nodes.items())
all_node_items.sort(key=lambda n: (n[0].line_idx, n[0].item_idx, n[0].fitness_class))
all_predecessor_node_keys: set[NodeKey] = set()  # used to make sure we only show nodes on feasible paths to end
for _, all_nodes_data in all_node_items:
    for node_data in all_nodes_data:
        if node_data.previous is not None:
            all_predecessor_node_keys.add(node_data.previous[0])

n_nodes = 0
for node_key, all_nodes_data in all_node_items:
    if node_key not in all_predecessor_node_keys and node_key.item_idx != len(para_items) - 1:
        continue
    n_nodes += 1

    if node_key.item_idx == len(para_items) - 1:
        item_label = "END"
    elif node_key.item_idx is None:
        item_label = "START"
    else:
        item_label = f"\"{''.join(item.text for item in para_items[max(0, node_key.item_idx - 1):node_key.item_idx + 1]).rstrip()}\" @ {node_key.item_idx}"

    if node_key.item_idx is not None:
        node_label = f"{item_label}\n{node_key.fitness_class.name}"
    else:
        node_label = item_label
    
    for node_data in all_nodes_data:
        node_attrs = {"shape": "box"}
        if node_key in node_keys_on_best_path:
            node_attrs["color"] = "red"
            node_attrs["fontcolor"] = "red"
            node_attrs["penwidth"] = "2"
        dot.node(f"{id(node_key)}", node_label, **node_attrs)
        
for node_key, all_nodes_data in all_nodes.items():
    if node_key not in all_predecessor_node_keys and node_key.item_idx != len(para_items) - 1:
        continue

    for node_data in all_nodes_data:
        if node_data.previous is None:
            continue
        edge_attrs = {}
        if node_key in node_keys_on_best_path and node_data.previous[0] in node_keys_on_best_path:
            edge_attrs["color"] = "red"
            edge_attrs["fontcolor"] = "red"
            edge_attrs["penwidth"] = "2"
        dot.edge(f"{id(node_data.previous[0])}", f"{id(node_key)}", f"{node_data.total_demerits:,.0f}", **edge_attrs)

print(f"Node count: {n_nodes}")

Node count: 541


In [11]:
if n_nodes < 200:
    display(dot)

In [12]:
greedy_line_break_idxs = list(greedy_line_breaks(para_items, line_width))
line_height = rm_size * 1.1
paper_size = (2 * (line_width + rm_font.em_size[0] * 5), line_height * (max(len(greedy_line_break_idxs), len(optimal_line_break_idxs)) + 2))

In [13]:
def draw_page(ctx: cairo.Context, line_break_idxs: Sequence[int], line_width: float, line_height: float):
    ctx.set_source_rgba(1, 0, 0, 0.5)
    ctx.set_line_width(1.0)

    ctx.move_to(rm_size, 0)
    ctx.rel_line_to(0, paper_size[1])
    ctx.move_to(rm_size + line_width, 0)
    ctx.rel_line_to(0, paper_size[1])
    ctx.close_path()
    ctx.stroke()
    
    ctx.set_source_rgb(0, 0, 0)
    render_lines(ctx, line_break_idxs, rm_size, 2*line_height, line_width)

svg_file = io.BytesIO()
with cairo.SVGSurface(svg_file, paper_size[0], paper_size[1]) as surface:
    ctx = cairo.Context(surface)
    ctx.set_source_rgb(1, 1, 1)
    ctx.rectangle(0, 0, paper_size[0], paper_size[1])
    ctx.fill()

    draw_page(ctx, greedy_line_break_idxs, line_width, line_height)
    ctx.translate(line_width + rm_font.em_size[0] * 5, 0)
    draw_page(ctx, optimal_line_break_idxs, line_width, line_height)
display(SVG(svg_file.getvalue()))

with cairo.PDFSurface("example.pdf", paper_size[0], paper_size[1]) as surface:
    ctx = cairo.Context(surface)
    ctx.set_source_rgb(1, 1, 1)
    ctx.rectangle(0, 0, paper_size[0], paper_size[1])
    ctx.fill()

    draw_page(ctx, greedy_line_break_idxs, line_width, line_height)
    ctx.translate(line_width + rm_font.em_size[0] * 5, 0)
    draw_page(ctx, optimal_line_break_idxs, line_width, line_height)